In [ ]:
!pip install git+https://github.com/RDFLib/sparqlwrapper

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/RDFLib/sparqlwrapper to /tmp/pip-req-build-2k6utawz
  Running command git clone --filter=blob:none --quiet https://github.com/RDFLib/sparqlwrapper /tmp/pip-req-build-2k6utawz
  Resolved https://github.com/RDFLib/sparqlwrapper to commit 2a6e2d3ddbc3fe38ca47d6d05f23c9b61ff82366
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 528.1/528.1 kB 29.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 41.7/41.7 kB 3.8 MB/s eta 0:00:00
  Created wheel for SPARQLWrapper: filename=SPARQLWrapper-2.0.1a0-py3-none-any.whl size=28648 sha256=a83b8744574459cf90d9a4aaab53521163cd8719203a2d6b6c9a197104a5b59a
  Stored in directory: /tmp/pip-ephem-wheel-cache-q7fialnd/wheels/64/db/31/75e25543c73b964f8882469c29b935f092182b765b6a0beb9f
Success

In [ ]:
import re
import csv

import pandas as pd
import numpy as np

from io import StringIO
import math
from tqdm import tqdm
import time

import sys

from urllib.error import HTTPError, URLError
from SPARQLWrapper import SPARQLWrapper, JSON, POST, GET, POSTDIRECTLY, CSV
# import fasttext 
# import fasttext.util
# import h5py
import pickle

In [ ]:
import pandas as pd
import numpy as np
import re
from sklearn.model_selection import train_test_split

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns

### SPARQL Extraction Utilities

In [ ]:
# SPARQL Extraction Utilities

def create_sparql_client(sparql_endpoint, http_query_method = GET, result_format= JSON):
    sparql_client = SPARQLWrapper(sparql_endpoint)

    sparql_client.setMethod(http_query_method)
    sparql_client.setReturnFormat(result_format)

    return sparql_client

# Convert SPARQL results into a Pandas data frame
def sparql2dataframe(json_sparql_results):
    cols = json_sparql_results['head']['vars']
    out = []
    for row in json_sparql_results['results']['bindings']:
        item = []
        for c in cols:
            item.append(row.get(c, {}).get('value'))
        out.append(item)
    return pd.DataFrame(out, columns=cols)

def query_sparql(query, sparql_client):
    sparql_client.setQuery(query)
    result_object = sparql_client.query()
    if sparql_client.returnFormat == JSON:
        return result_object._convertJSON() 
    return result_object.convert()

## Generate TD1

Split s-p-o triples file such that there are no entities in test set that are not present in training set



In [ ]:
!unzip spo_triples_iter1.zip

Archive:  spo_triples_iter1.zip
replace spo_triples_iter1.csv? [y]es, [n]o, [A]ll, [N]one, [r]ename: y
  inflating: spo_triples_iter1.csv   


In [ ]:
# load all matched s-p-o triples
data = pd.read_csv('spo_triples_iter1.zip')
data.head()

subject       predicate          object
0   wkg:656260805  wkgs:addrPlace  wkg:1586413209
1  wkg:8423662676  wkgs:addrPlace   wkg:362658024
2  wkg:3722193229  wkgs:addrPlace  wkg:3009719004
3  wkg:2995637431  wkgs:addrPlace  wkg:3009701150
4  wkg:4063046696  wkgs:addrPlace    wkg:31345707

In [ ]:
# clean namespace of uri of some triples
pattern = '^http://www.worldkg.org/resource/'
compiled_pattern = re.compile(pattern)

data['object'] = data['object'].apply(lambda uri: re.sub(compiled_pattern, 'wkg:', uri))
data.head()


subject       predicate          object
0   wkg:656260805  wkgs:addrPlace  wkg:1586413209
1  wkg:8423662676  wkgs:addrPlace   wkg:362658024
2  wkg:3722193229  wkgs:addrPlace  wkg:3009719004
3  wkg:2995637431  wkgs:addrPlace  wkg:3009701150
4  wkg:4063046696  wkgs:addrPlace    wkg:31345707

In [ ]:
data['predicate'].value_counts()

wkgs:isInCountry        247524
wkgs:isInContinent       73965
wkgs:isIn                31935
wkgs:addrPlace           22186
wkgs:country              7461
wkgs:addrState            3104
wkgs:isInCounty           3066
wkgs:addrSuburb           2284
wkgs:addrProvince          797
wkgs:capitalCity           166
wkgs:addrSubdistrict       104
wkgs:addrCountry            52
wkgs:addrDistrict           48
wkgs:addrHamlet             38
Name: predicate, dtype: int64

In [ ]:
data.shape

(392730, 3)

In [ ]:
# create stratified split on the basis of predicates - 70/30 split
predicates = data['predicate']
train_val_triples, test_triples = train_test_split(data, stratify = predicates, test_size = 0.3, random_state = 0)

# create train-val set  - 90/10 split
predicates = train_val_triples['predicate']
train_triples, val_triples = train_test_split(train_val_triples, stratify = predicates, test_size = 0.1, random_state = 0)

In [ ]:
# list all entities (subject or object) present in train triples
training_entities, train_entities_counts = np.unique(train_triples[['subject', 'object']].values.flatten(), return_counts = True)

In [ ]:
training_entities.shape

(223297,)

In [ ]:
# filter validation triples
val_filtered_triples = val_triples[val_triples['subject'].isin(training_entities) & val_triples['object'].isin(training_entities)]
val_filtered_triples.reset_index(drop=True, inplace=True)

In [ ]:
val_filtered_triples.shape

(6145, 3)

In [ ]:
test_triples.shape

(117819, 3)

In [ ]:
test_triples['predicate'].value_counts()

wkgs:isInCountry        74257
wkgs:isInContinent      22190
wkgs:isIn                9581
wkgs:addrPlace           6656
wkgs:country             2238
wkgs:addrState            931
wkgs:isInCounty           920
wkgs:addrSuburb           685
wkgs:addrProvince         239
wkgs:capitalCity           50
wkgs:addrSubdistrict       31
wkgs:addrCountry           16
wkgs:addrDistrict          14
wkgs:addrHamlet            11
Name: predicate, dtype: int64

In [ ]:
# filter test triples
test_filtered_triples = test_triples[test_triples['subject'].isin(training_entities) & test_triples['object'].isin(training_entities)]
test_filtered_triples.reset_index(drop=True, inplace=True)

In [ ]:
test_filtered_triples.shape

(26087, 3)

In [ ]:
test_filtered_triples['predicate'].value_counts()

wkgs:isInCountry      13057
wkgs:isInContinent    12918
wkgs:isIn                69
wkgs:isInCounty          32
wkgs:capitalCity         11
Name: predicate, dtype: int64

In [ ]:
# verification whether all entities in test set are in training
test_filtered_entities = np.unique(test_filtered_triples[['subject', 'object']].values.flatten(), return_counts = False)
x = np.isin(test_filtered_entities, training_entities)
x

array([ True,  True,  True, ...,  True,  True,  True])

In [ ]:
x.shape

(26185,)

In [ ]:
test_filtered_entities.shape

(26185,)

In [ ]:
val_filtered_triples.head()

subject           predicate         object
0  wkg:3956554717    wkgs:isInCountry  wkg:424298311
1  wkg:4429160380    wkgs:isInCountry  wkg:424298311
2  wkg:4453896599  wkgs:isInContinent   wkg:36966065
3  wkg:4413975592  wkgs:isInContinent   wkg:36966065
4  wkg:4449327867    wkgs:isInCountry  wkg:424298311

In [ ]:
# verfication - validation entities appear in training
val_filtered_entities = val_filtered_triples[['subject', 'object']].values.flatten()
x = np.isin(val_filtered_entities, training_entities)
x

array([ True,  True,  True, ...,  True,  True,  True])

In [ ]:
# Save train, test and validation triples in txt file
train_triples.to_csv('train.txt', sep = '\t', index=False, header = False)
val_filtered_triples.to_csv('valid.txt', sep = '\t', index = False, header = False)
test_filtered_triples.to_csv('test.txt', sep = '\t', index = False, header = False)

In [ ]:
unique_entities_in_test = np.unique(test_filtered_triples[['subject', 'object']].values.flatten(), return_counts = False)
unique_entities_in_test.shape

(26185,)

In [ ]:
test_filtered_triples['predicate'].value_counts()

wkgs:isInCountry      13057
wkgs:isInContinent    12918
wkgs:isIn                69
wkgs:isInCounty          32
wkgs:capitalCity         11
Name: predicate, dtype: int64

## Create numerical and text literals txt file

In [ ]:
##
# Changes for Split 2
##

train_triples = pd.read_csv('train.txt', sep = '\t', names = ['subject', 'predicate', 'object'])
train_triples

subject         predicate          object
0        wkg:501484122  wkgs:isInCountry   wkg:424316663
1       wkg:1308600217  wkgs:isInCountry  wkg:6677037562
2       wkg:2016097408  wkgs:isInCountry   wkg:248120384
3       wkg:1070163307  wkgs:isInCountry  wkg:6677037562
4        wkg:309872497         wkgs:isIn   wkg:424298326
...                ...               ...             ...
323061  wkg:1070187198  wkgs:isInCountry  wkg:6677037562
323062   wkg:501520502  wkgs:isInCountry   wkg:424316663
323063  wkg:1308321070  wkgs:isInCountry  wkg:6677037562
323064  wkg:1070158119  wkgs:isInCountry  wkg:6677037562
323065   wkg:501286883  wkgs:isInCountry   wkg:424316663

[323066 rows x 3 columns]

In [ ]:
training_entities = np.unique(train_triples[['subject', 'object']].values.flatten(), return_counts = False)
training_entities.shape

(284305,)

In [ ]:
training_entities

array(['wkg:1000062530', 'wkg:1000181671', 'wkg:100035698', ...,
       'wkg:999070106', 'wkg:999260139', 'wkg:999508403'], dtype=object)

## Fetch all literal triples using SPARQL

In [ ]:
sparqlview_endpoint = "https://www.worldkg.org/sparql"
sparqlview_wrapper = create_sparql_client(sparql_endpoint=sparqlview_endpoint)

In [ ]:
# extract all triples for each unique entity

batch_size = 100
batches = math.ceil(len(training_entities)/batch_size)

results_df_list = []
for i in tqdm(range(batches)):
  selected_entities = training_entities[i*100: (i+1)*100]
  selected_entities_string = ' '.join(selected_entities)
  query  =  """
  PREFIX uom: <http://www.opengis.net/def/uom/OGC/1.0/>
  PREFIX wkgs: <http://www.worldkg.org/schema/>
  PREFIX wkg: <http://www.worldkg.org/resource/>
  PREFIX wd: <http://www.wikidata.org/wiki/>
  PREFIX sf: <http://www.opengis.net/ont/sf#>
  PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
  PREFIX geo: <http://www.opengis.net/ont/geosparql#>
  PREFIX owl: <http://www.w3.org/2002/07/owl#>
  PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
  SELECT DISTINCT ?subject ?predicate ?object WHERE {
      VALUES ?subject {%s}.
      ?subject ?predicate ?object.
  }
  """%(selected_entities_string)
  print(query)
  try:
    results = query_sparql(query,sparqlview_wrapper)
  except Exception as e:
    print(sys.exc_info()[0])
    print(e)

  results_df = sparql2dataframe(results)
  print(results_df.shape)
  results_df_list.append(results_df)


merged_results = pd.concat(results_df_list, ignore_index = True)

# remove duplicate rows from merged_results
merged_results = merged_results[~merged_results.duplicated(keep = 'first')].reset_index(drop = True)
merged_results.shape

  0%|          | 0/2844 [00:00<?, ?it/s]


  PREFIX uom: <http://www.opengis.net/def/uom/OGC/1.0/>
  PREFIX wkgs: <http://www.worldkg.org/schema/>
  PREFIX wkg: <http://www.worldkg.org/resource/>
  PREFIX wd: <http://www.wikidata.org/wiki/>
  PREFIX sf: <http://www.opengis.net/ont/sf#>
  PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
  PREFIX geo: <http://www.opengis.net/ont/geosparql#>
  PREFIX owl: <http://www.w3.org/2002/07/owl#>
  PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
  SELECT DISTINCT ?subject ?predicate ?object WHERE {
      VALUES ?subject {wkg:1000062530 wkg:1000181671 wkg:100035698 wkg:1000800826 wkg:1000800871 wkg:1000819151 wkg:1000843206 wkg:1000843240 wkg:1001317615 wkg:10021976 wkg:1003705119 wkg:1003706857 wkg:1003794873 wkg:1003799115 wkg:1003816037 wkg:1003818299 wkg:1003848278 wkg:1004107872 wkg:1004366085 wkg:1005022115 wkg:1005043221 wkg:1005374048 wkg:1005660304 wkg:1005667968 wkg:1005771142 wkg:1005771185 wkg:1005788090 wkg:1005960840 wkg:100628304 wkg:100628318 wkg:100628319 wkg

  0%|          | 1/2844 [00:00<42:14,  1.12it/s]

(890, 3)

  PREFIX uom: <http://www.opengis.net/def/uom/OGC/1.0/>
  PREFIX wkgs: <http://www.worldkg.org/schema/>
  PREFIX wkg: <http://www.worldkg.org/resource/>
  PREFIX wd: <http://www.wikidata.org/wiki/>
  PREFIX sf: <http://www.opengis.net/ont/sf#>
  PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
  PREFIX geo: <http://www.opengis.net/ont/geosparql#>
  PREFIX owl: <http://www.w3.org/2002/07/owl#>
  PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
  SELECT DISTINCT ?subject ?predicate ?object WHERE {
      VALUES ?subject {wkg:1012680033 wkg:1012680179 wkg:1012680262 wkg:1012680310 wkg:1012761434 wkg:1012851535 wkg:1012885131 wkg:1013099712 wkg:1013176773 wkg:1013230295 wkg:1013230320 wkg:1013433648 wkg:1013494933 wkg:1013516859 wkg:1013517210 wkg:1013550821 wkg:1013551041 wkg:1013581128 wkg:1013641504 wkg:1013645659 wkg:1013645811 wkg:1013649727 wkg:1013912389 wkg:1013983923 wkg:1014625648 wkg:101480194 wkg:1014890255 wkg:1014890336 wkg:1014890380 wkg:1014890421 wkg:

  0%|          | 2/2844 [00:01<39:34,  1.20it/s]

...

100%|█████████▉| 2843/2844 [32:21<00:00,  1.38it/s]

(745, 3)

  PREFIX uom: <http://www.opengis.net/def/uom/OGC/1.0/>
  PREFIX wkgs: <http://www.worldkg.org/schema/>
  PREFIX wkg: <http://www.worldkg.org/resource/>
  PREFIX wd: <http://www.wikidata.org/wiki/>
  PREFIX sf: <http://www.opengis.net/ont/sf#>
  PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
  PREFIX geo: <http://www.opengis.net/ont/geosparql#>
  PREFIX owl: <http://www.w3.org/2002/07/owl#>
  PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
  SELECT DISTINCT ?subject ?predicate ?object WHERE {
      VALUES ?subject {wkg:998380682 wkg:998509115 wkg:999070106 wkg:999260139 wkg:999508403}.
      ?subject ?predicate ?object.
  }
  


100%|██████████| 2844/2844 [32:21<00:00,  1.46it/s]

(38, 3)


(2186630, 3)

In [ ]:
merged_results

subject  \
0        http://www.worldkg.org/resource/1003705119   
1        http://www.worldkg.org/resource/1003706857   
2         http://www.worldkg.org/resource/100628304   
3         http://www.worldkg.org/resource/100628318   
4         http://www.worldkg.org/resource/100628319   
...                                             ...   
2186625   http://www.worldkg.org/resource/998509115   
2186626   http://www.worldkg.org/resource/999070106   
2186627   http://www.worldkg.org/resource/998380682   
2186628   http://www.worldkg.org/resource/998509115   
2186629   http://www.worldkg.org/resource/999070106   

                                               predicate  \
0        http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
1        http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
2        http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
3        http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
4        http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
...                                                  ...   
2186625           http://www.worldkg.org/schema/wikidata   
2186626           http://www.worldkg.org/schema/wikidata   
2186627          http://www.worldkg.org/schema/wikipedia   
2186628          http://www.worldkg.org/schema/wikipedia   
2186629          http://www.worldkg.org/schema/wikipedia   

                                                    object  
0                    http://www.worldkg.org/schema/Village  
1                    http://www.worldkg.org/schema/Village  
2              http://www.worldkg.org/schema/Neighbourhood  
3              http://www.worldkg.org/schema/Neighbourhood  
4              http://www.worldkg.org/schema/Neighbourhood  
...                                                    ...  
2186625             http://www.wikidata.org/wiki/Q28526167  
2186626              http://www.wikidata.org/wiki/Q6615802  
2186627  https://ru.wikipedia.org/wiki/ru%3A%25D0%259F%...  
2186628  https://ru.wikipedia.org/wiki/ru%3A%25D0%2591%...  
2186629  https://tr.wikipedia.org/wiki/tr%3AKirazl%25C4...  

[2186630 rows x 3 columns]

In [ ]:
# remove/change uri prefix from triples
pattern = '^http://www.worldkg.org/schema/'
compiled_pattern = re.compile(pattern)

# merged_results['subject'] = merged_results['subject'].apply(lambda uri: re.sub(compiled_pattern, 'wkg:', uri))
merged_results['predicate'] = merged_results['predicate'].apply(lambda uri: re.sub(compiled_pattern, 'wkgs:', uri))
merged_results['object'] = merged_results['object'].apply(lambda uri: re.sub(compiled_pattern, 'wkgs:', uri))
merged_results

subject  \
0        http://www.worldkg.org/resource/1003705119   
1        http://www.worldkg.org/resource/1003706857   
2         http://www.worldkg.org/resource/100628304   
3         http://www.worldkg.org/resource/100628318   
4         http://www.worldkg.org/resource/100628319   
...                                             ...   
2186625   http://www.worldkg.org/resource/998509115   
2186626   http://www.worldkg.org/resource/999070106   
2186627   http://www.worldkg.org/resource/998380682   
2186628   http://www.worldkg.org/resource/998509115   
2186629   http://www.worldkg.org/resource/999070106   

                                               predicate  \
0        http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
1        http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
2        http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
3        http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
4        http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
...                                                  ...   
2186625                                    wkgs:wikidata   
2186626                                    wkgs:wikidata   
2186627                                   wkgs:wikipedia   
2186628                                   wkgs:wikipedia   
2186629                                   wkgs:wikipedia   

                                                    object  
0                                             wkgs:Village  
1                                             wkgs:Village  
2                                       wkgs:Neighbourhood  
3                                       wkgs:Neighbourhood  
4                                       wkgs:Neighbourhood  
...                                                    ...  
2186625             http://www.wikidata.org/wiki/Q28526167  
2186626              http://www.wikidata.org/wiki/Q6615802  
2186627  https://ru.wikipedia.org/wiki/ru%3A%25D0%259F%...  
2186628  https://ru.wikipedia.org/wiki/ru%3A%25D0%2591%...  
2186629  https://tr.wikipedia.org/wiki/tr%3AKirazl%25C4...  

[2186630 rows x 3 columns]

## Clean literal triples

In [ ]:
!unzip all_literal_triples.zip

Archive:  all_literal_triples.zip
replace all_literal_triples.csv? [y]es, [n]o, [A]ll, [N]one, [r]ename: y
  inflating: all_literal_triples.csv  


In [ ]:
# literal_triples = pd.read_csv('all_literal_triples.zip')
literal_triples = merged_results

In [ ]:
# clean namespace of uri of some triples
pattern = '^http://www.worldkg.org/resource/'
compiled_pattern = re.compile(pattern)

literal_triples['subject'] = literal_triples['subject'].apply(lambda uri: re.sub(compiled_pattern, 'wkg:', uri))
literal_triples.head()

subject                                        predicate  \
0  wkg:1003705119  http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
1  wkg:1003706857  http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
2   wkg:100628304  http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
3   wkg:100628318  http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
4   wkg:100628319  http://www.w3.org/1999/02/22-rdf-syntax-ns#type   

               object  
0        wkgs:Village  
1        wkgs:Village  
2  wkgs:Neighbourhood  
3  wkgs:Neighbourhood  
4  wkgs:Neighbourhood

In [ ]:
literal_triples.shape

(2186630, 3)

In [ ]:
# filter out literal triples where subject is in training_entities, all others are irrelevant
literal_triples = literal_triples[literal_triples['subject'].isin(training_entities)]
literal_triples.reset_index(drop=True, inplace=True)

In [ ]:
literal_triples.shape

(1702678, 3)

In [ ]:
predicates_in_spo = train_triples['predicate'].value_counts().index.values
predicates_in_spo

array(['wkgs:isInCountry', 'wkgs:isInContinent', 'wkgs:isIn',
       'wkgs:addrPlace', 'wkgs:addrCountry', 'wkgs:country',
       'wkgs:addrState', 'wkgs:isInCounty', 'wkgs:addrSuburb',
       'wkgs:addrProvince', 'wkgs:capitalCity', 'wkgs:addrSubdistrict',
       'wkgs:addrDistrict', 'wkgs:addrHamlet'], dtype=object)

In [ ]:
# remove triples containing one of the 14 selected predicates from spo
literal_triples = literal_triples[~literal_triples['predicate'].isin(predicates_in_spo)]
literal_triples.reset_index(drop = True, inplace = True)

In [ ]:
literal_triples['predicate'].value_counts()

wkgs:osmLink                                       284205
wkgs:spatialObject                                 284205
http://www.w3.org/2000/01/rdf-schema#label         257375
http://www.w3.org/1999/02/22-rdf-syntax-ns#type    255149
wkgs:source                                        108877
                                                    ...  
wkgs:seamarkRadarTransponderGroup                       1
wkgs:seamarkRadarTransponderCategory                    1
wkgs:service                                            1
wkgs:fountain                                           1
wkgs:tents                                              1
Name: predicate, Length: 422, dtype: int64

In [ ]:
literal_triples.head()

subject                                        predicate  \
0  wkg:1003705119  http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
1  wkg:1003706857  http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
2   wkg:100628304  http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
3   wkg:100628318  http://www.w3.org/1999/02/22-rdf-syntax-ns#type   
4   wkg:100628319  http://www.w3.org/1999/02/22-rdf-syntax-ns#type   

               object  
0        wkgs:Village  
1        wkgs:Village  
2  wkgs:Neighbourhood  
3  wkgs:Neighbourhood  
4  wkgs:Neighbourhood

In [ ]:
def clean_coordinates(df, coord_col):
  '''
  :param df - input dataframe
  return clean_df - dataframe with separate columns for 'lat' and 'lon'
  '''
  # applying regex to remove 'Point(' and ')'
  pattern = '(POINT\()|(\))'
  compiled_pattern = re.compile(pattern)
  df['lon_lat'] = df[coord_col].apply(lambda value: re.sub(compiled_pattern, '', value).split(' '))

  # creating separate columns for lon and lat and convert lat lon columns to float
  df[['wkgs:lon', 'wkgs:lat']] = pd.DataFrame(df['lon_lat'].to_list(), index = df.index)
  df['wkgs:lat'] = df['wkgs:lat'].astype('float')
  df['wkgs:lon'] = df['wkgs:lon'].astype('float')
  df.drop(['lon_lat'], inplace = True, axis = 1)

  return df

In [ ]:
spatial_triples = literal_triples[literal_triples['predicate'] == 'wkgs:spatialObject']
spatial_triples.reset_index(drop = True, inplace = True)
spatial_triples = clean_coordinates(spatial_triples, coord_col = 'object')
spatial_triples

In [ ]:
spatial_triples.shape

In [ ]:
spatial_triples_melted = pd.melt(spatial_triples, id_vars=['subject'], value_vars=['wkgs:lon', 'wkgs:lat'], var_name='predicate', value_name='object')

In [ ]:
spatial_triples_melted

In [ ]:
# now separate row exisits to store lat and lon
spatial_triples_melted[spatial_triples_melted['subject'] == 'wkg:1860825766']

In [ ]:
# merge spatial triples with literal triples and delete redundant rows
literal_triples = pd.concat([literal_triples, spatial_triples_melted], ignore_index=True)
literal_triples = literal_triples[literal_triples['predicate'] != 'wkgs:spatialObject']
literal_triples.reset_index(drop = True, inplace = True)

In [ ]:
literal_triples['predicate'].value_counts()

In [ ]:
# split into numeric literal triples and text literal triples
is_triple_object_non_numeric_mask = pd.to_numeric(literal_triples['object'], errors='coerce').isna()
text_literal_triples = literal_triples[is_triple_object_non_numeric_mask]
numeric_literal_triples = literal_triples[~is_triple_object_non_numeric_mask]

In [ ]:
a = numeric_literal_triples[numeric_literal_triples['predicate'] == 'wkgs:lon']['object'].iloc[0]

In [ ]:
type(a)

In [ ]:
pd.to_numeric(numeric_literal_triples[numeric_literal_triples['predicate'] == 'wkgs:lon']['object'], errors='coerce').isna()

In [ ]:
# Save numerical_literals and text_literals and combined literals as txt
numeric_literal_triples.to_csv('numerical_literals.txt', sep = '\t', index = False, header = False)
text_literal_triples.to_csv('text_literals.txt', sep = '\t', index = False, header = False)

In [ ]:
print(f'numeric_literal_triples.shape {numeric_literal_triples.shape}')
print(f'text_literal_triples.shape {text_literal_triples.shape}')


In [ ]:
# save combined literal triples
combined_literal_triples = pd.concat([numeric_literal_triples, text_literal_triples], ignore_index=True)
combined_literal_triples.to_csv('combined_literal_triples.txt', sep = '\t', index = False, header = False)

## Preprocess text literals

In [ ]:
import pandas as pd
import numpy as np

In [ ]:
text_literal_triples = pd.read_csv('text_literals.txt', header = None, sep = '\t', names = ['subject', 'predicate', 'object'])
text_literal_triples

In [ ]:
# remove triples where object is NaN
text_literal_triples = text_literal_triples[~pd.isna(text_literal_triples['object'])]
text_literal_triples.reset_index(drop = True, inplace = True)
text_literal_triples

In [ ]:
text_literal_triples.to_csv('text_literals.txt', sep = '\t', index = False, header = False)